In [1]:
#!pip install pyproj
#!pip install request

# MANUAL SKETCHBOOK

La finalidad de este software es completar la mayor cantidad de información del estandar Darwin Core a partir de un par de coordenadas, *importante hacer notar que este software hasta el momento no realiza ningun tipo de georreferenciación, solo rellena datos*, esto se realiza a partir de un set de coordenadas, esta pueden ser del campo verbatimCoordinates o decimalLatitude y decimalLongitude, pertenecientes al estandar. Con estos datos será completar los siguientes campos, si es que se encuentra la información necesaria. 

- higherGeography 
- continent 
- country 
- countryCode 
- stateProvince 
- county 
- municipality 
- decimalLongitude, decimalLatitude
- geodeticDatum 
- coordinatePrecision 
- verbatimLatitude, verbatimLongitude
- verbatimCoordinateSystem 

Hasta el momento no se ha podido probar la localización de localidades marinas, pero es un trabajo en progreso. 

Este script se divide en dos clases

- Preparación de la base de datos (db_prep)
- Transformación de coordenadas (coord_transform) 

## Preparación de la base de datos

Esta clase recibe el nombre de "db_prep" y necesita como entrada una base de datos con algunos componentes mínimos del estandar Darwin Core (DwC) para su realización.



## Transformación de coordenadas 

- La base de datos debe tener los siguientes campos llenos de manera obligatorioa.
    - verbatimCoordinates (desde esté campo se hará la transformación).
    - verbatimCoordinateSystem
    - country
    

In [2]:
from pyproj import Proj #no se está usando por el momento
import utm
import requests
import json
import pandas as pd
import numpy as np
import math
import re
from geopy.geocoders import Nominatim #FASTER than api



pd.set_option('display.max_columns', None)  # or 1000
pd.set_option('display.max_rows', None)  # or 1000
pd.set_option('display.max_colwidth', None)  # or 199

country_data=pd.read_csv("https://raw.githubusercontent.com/VertNet/DwCVocabs/master/vocabs/countryCode_country_continent_merged.csv")
country_data.set_index("country",inplace=True)
country_data_dict=country_data.to_dict()

In [3]:
class db_prep:
    def __init__(self,data):
        self.data=data
    
    def verbatimCoordinates_dms_sep(self,index):
        for Coordinate in self.data.loc[index,"verbatimCoordinates"].split(","):
            if "N" in Coordinate.upper(): 
                self.data.loc[index,"verbatimLatitude"]=Coordinate
            elif "S" in Coordinate.upper(): 
                self.data.loc[index,"verbatimLatitude"]=Coordinate
            elif "E" in Coordinate.upper(): 
                self.data.loc[index,"verbatimLongitude"]=Coordinate
            elif "W" or "O" in Coordinate.upper(): 
                self.data.loc[index,"verbatimLongitude"]=Coordinate

    
    def verbatimCoordinates_utm_sep(self,index):
        Coordinate= self.data.loc[index,"verbatimCoordinates"].split(" ")
        for elements in coordinate:
            if "N" or "S" in elements.upper(): timezone_index=coordinate.index(elements)
        Coordinate_indexes=list(range(0,len(Coordinate)))
        Coordinate_indexes.remove(timezone_index)
        if int(Coordinate[Coordinate_indexes[0]]) > int(Coordinate[Coordinate_indexes[1]]):
            self.data.loc[index,"verbatimLatitude"]=Coordinate[Coordinate_indexes[1]]
            self.data.loc[index,"verbatimLongitude"]=Coordinate[Coordinate_indexes[0]]
        else:
            self.data.loc[index,"verbatimLatitude"]=Coordinate[0]
            self.data.loc[index,"verbatimLongitude"]=Coordinate[1]
    
    def verb_lat_long_autocomplete(self):
        if set(['verbatimLatitude', 'verbatimLongitude']).issubset(set(self.data.columns.to_list())) is False:
            verb_coord_position=self.data.columns.to_list().index("verbatimCoordinates")+1
            self.data.insert(verb_coord_position,"verbatimLatitude",np.nan)
            self.data.insert(verb_coord_position+1,"verbatimLongitude",np.nan)
            for index in self.data.index:
                if self.data.loc[index,"verbatimCoordinates"] is np.nan:
                    pass
                elif isinstance(self.data.loc[index,"verbatimLongitude"],str)==False and isinstance(self.data.loc[index,"verbatimLatitude"],str)==False:  #cambio
                    if (np.isnan(self.data.loc[index,"verbatimLongitude"])) or (np.isnan(self.data.loc[index,"verbatimLatitude"])): #cambio
                        if self.data.loc[index,"verbatimCoordinateSystem"]=="UTM":
                            self.verbatimCoordinates_utm_sep()
                        elif self.data.loc[index,"verbatimCoordinateSystem"]=="degrees minutes seconds":
                                self.verbatimCoordinates_dms_sep()
                        else:
                            pass                    
        if set(['verbatimLatitude', 'verbatimLongitude']).issubset(set(self.data.columns.to_list())) is True:
            for index in self.data.index:
                if self.data.loc[index,"verbatimCoordinates"] is np.nan:
                    pass
                elif isinstance(self.data.loc[index,"verbatimLongitude"],str)==False and isinstance(self.data.loc[index,"verbatimLatitude"],str)==False:  #cambio
                    if (np.isnan(self.data.loc[index,"verbatimLongitude"])) or (np.isnan(self.data.loc[index,"verbatimLatitude"])): #cambio
                        if self.data.loc[index,"verbatimCoordinateSystem"]=="UTM":
                            self.verbatimCoordinates_utm_sep(index)
                        elif self.data.loc[index,"verbatimCoordinateSystem"]=="degrees minutes seconds":
                            self.verbatimCoordinates_dms_sep(index)
                        else:
                            pass
                        
    
    def continent_autocomplete(self):
        country_data=pd.read_csv("https://raw.githubusercontent.com/VertNet/DwCVocabs/master/vocabs/countryCode_country_continent_merged.csv")
        country_data.set_index("country",inplace=True)
        country_data_dict=country_data.to_dict()
        if set(['country']).issubset(set(self.data.columns.to_list())) is True:
            if set(['continent']).issubset(set(self.data.columns.to_list())) is True:
                for index in self.data.index:
                    if self.data.loc[index,"country"] in country_data_dict["continent"].keys() and self.data.loc[index,"continent"] is np.nan:
                        self.data.loc[index,"continent"]=country_data_dict["continent"][self.data.loc[index,"country"]]
                    else: pass        
            elif set(['continent']).issubset(set(self.data.columns.to_list())) is False:
                self.data.insert(self.data.columns.to_list().index("country")-1,"continent",np.nan) #en que lugar lo coloco
                for index in self.data.index:
                    if self.data.loc[index,"country"] in country_data_dict["continent"].keys():
                        self.data.loc[index,"continent"]=country_data_dict["continent"][self.data.loc[index,"country"]]
                    else: pass  
        else: pass 
    
    def location_autocomplete(self): #include country, country_code, stateProvince, county, municipality 
        for index in self.data.index:
            try:
                lat=self.data.loc[index,"decimalLatitude"]
                lon=self.data.loc[index,"decimalLongitude"]
                result=requests.get(f"https://api.gbif-uat.org/v1/geocode/reverse?lat={lat}&lng={lon}").json()
                print(f"{index} exito")
                for elements in result:
                    if elements["source"]=="http://gadm.org/":
                        print(f"{index} exito")
                        if elements["type"]=="GADM0":
                            self.data.loc[index,"country"]=elements["title"]
                            self.data.loc[index,"countryCode"]=elements["isoCountryCode2Digit"]
                        elif elements["type"]=="GADM1": self.data.loc[index,"stateProvince"]=elements["title"]
                        elif elements["type"]=="GADM2": self.data.loc[index,"county"]=elements["title"]
                        elif elements["type"]=="GADM3": self.data.loc[index,"municipality"]=elements["title"]
            except: 
                print(f"{index} fail")
                pass
        
    def higherGeography_autocomplete(self): 
        dwc_labels=["continent","waterBody","country","stateProvince","county","municipality","islandGroup","island"]
        dwc_labels_selected=[i for i in dwc_labels if i in self.data.columns]
        try:
            for index in self.data.index:
                higherGeography_list=[]
                if self.data.loc[index,"higherGeography"] is not np.nan:
                    for elements in dwc_labels_selected:
                        if isinstance(self.data.loc[index,elements], str): higherGeography_list.append(self.data.loc[index,elements])
                higherGeography_str=" | ".join(higherGeography_list)
                self.data.loc[index,"higherGeography"]=higherGeography_str         
        except KeyError:
            self.data["higherGeography"]=np.nan
            for index in self.data.index:
                higherGeography_list=[]
                if self.data.loc[index,"higherGeography"] is not np.nan:
                    for elements in dwc_labels_selected:
                        if isinstance(self.data.loc[index,elements], str): higherGeography_list.append(self.data.loc[index,elements])
                higherGeography_str=" | ".join(higherGeography_list)
                self.data.loc[index,"higherGeography"]=higherGeography_str      
    
    def verbatimCoordinates_autocomplete(self):
        if "verbatimCoordinates" not in self.data.columns:
            if "verbatimLatitude" and "verbatimLongitude" in self.data.columns:
                self.data["verbatimCoordinates"]=np.nan
                for index in self.data.index:
                    if self.data.loc[index,"verbatimLatitude"] and self.data.loc[index,"verbatimLongitude"] is not np.nan:
                        lat,lon=self.data.loc[index,"verbatimLatitude"],self.data.loc[index,"verbatimLongitude"]
                        self.data.loc[index,"verbatimCoordinates"]=f"{lat}, {lon}"
                    elif self.data.loc[index,"decimalLatitude"] and self.data.loc[index,"decimalLongitude"] is not np.nan:
                        lat,lon=self.data.loc[index,"decimalLatitude"],self.data.loc[index,"decimalLongitude"]
                        self.data.loc[index,"verbatimCoordinates"]=f"{lat}, {lon}"
                    else :pass 
        if "verbatimCoordinates" in self.data.columns:
            for index in self.data.index:
                if self.data.loc[index,"verbatimCoordinates"] is np.nan:
                    if self.data.loc[index,"verbatimLatitude"] and self.data.loc[index,"verbatimLongitude"] is not np.nan:
                        lat,lon=self.data.loc[index,"verbatimLatitude"],self.data.loc[index,"verbatimLongitude"]
                        self.data.loc[index,"verbatimCoordinates"]=f"{lat}, {lon}"
                    else: pass
                      
    def verbatimCoordinateSystem_autocomplete(self): #work in progress
        minutes="'"
        seconds='"'
        for index in self.data.index:
            try:
                if "°" or "d" in self.data.loc[index,"verbatimCoordinates"]: 
                    if minutes and seconds in self.data.loc[index,"verbatimCoordinates"]: self.data.loc[index,"verbatimCoordinateSystem"]="degrees minutes seconds"
                    elif minutes in self.data.loc[index,"verbatimCoordinates"]: self.data.loc[index,"verbatimCoordinateSystem"]="degrees decimal minutes"
                elif "." in self.data.loc[index,"verbatimCoordinates"]: self.data.loc[index,"verbatimCoordinateSystem"]="decimal degrees"
                else: self.data.loc[index,"verbatimCoordinateSystem"]="UTM"
            except: pass
    
    def coordinatePrecision_autocomplete(self):
        for index in self.data.index:
            if (self.data.loc[index,"verbatimLatitude"] or self.data.loc[index,"verbatiLongitude"]) is np.nan or self.data.loc[index,"verbatimCoordinateSystem"]=="decimal degrees":
                if (self.data.loc[index,"decimalLatitude"] or self.data.loc[index,"decimalLongitude"]) is not np.nan:
                    try:
                        lat=self.data.loc[index,"decimalLatitude"].split(".")
                        lon=self.data.loc[index,"decimalLongitude"].split(".")
                        self.data.loc[index,"coordinatePrecision"]="0."+"0"*(min(len(lat[1]),len(lon[1]))-1)+"1"
                    except: pass
            if self.data.loc[index,"verbatimCoordinateSystem"]=="degrees minutes seconds":
                try:
                    lat=self.data.loc[index,"verbatimLatitude"]
                    lon=self.data.loc[index,"verbatimLongitude"]
                    srch="'(.+?)\""
                    m_lat=re.search(srch, lat)
                    m_lon=re.search(srch, lon)
                    found_lat=m_lat.group(1)
                    found_lon=m_lon.group(1)
                    if "." in found_lat: 
                        pres=1/pow(10,len(found_lat.split(".")[1]))
                        coordP_lat=pres/3600.
                    else: coordP_lat=1/3600.
                    if "." in found_lon:
                        pres=1/pow(10,len(found_lon.split(".")[1]))
                        coordP_lon=pres/3600.
                    else: coordP_lon=1/3600.
                    self.data.loc[index,"coordinatePrecision"]='{:.7f}'.format(min(coordP_lon,coordP_lat))
                except: pass
            if self.data.loc[index,"verbatimCoordinateSystem"]=="degrees decimal minutes":
                try:
                    lat=self.data.loc[index,"verbatimLatitude"]
                    lon=self.data.loc[index,"verbatimLongitude"]
                    srch="°(.+?)\'"
                    m_lat=re.search(srch, lat)
                    m_lon=re.search(srch, lon)
                    found_lat=m_lat.group(1)
                    found_lon=m_lon.group(1)
                    if "." in found_lat: 
                        pres=1/pow(10,len(found_lat.split(".")[1]))
                        coordP_lat=pres/60.
                    else: coordP_lat=1/60.
                    if "." in found_lon:
                        pres=1/pow(10,len(found_lon.split(".")[1]))
                        coordP_lon=pres/60.
                    else: coordP_lon=1/60.
                    self.data.loc[index,"coordinatePrecision"]='{:.7f}'.format(min(coordP_lon,coordP_lat))
                except: pass

                

In [4]:
class coord_transform:
    def __init__(self,data):
        self.data=data
    
    def utm_to_dg(self):
        for index in self.data.index:
            if self.data.loc[index,"verbatimCoordinates"] is not np.nan and self.data.loc[index,"verbatimCoordinateSystem"]=="UTM":
                coordinate= self.data.loc[index,"verbatimCoordinates"].split(" ")
                for elements in coordinate:
                    if "N" in elements.upper(): 
                        zone_index=coordinate.index(elements)
                        Global="North"
                    elif "S" in elements.upper():
                        zone_index=coordinate.index(elements)
                        Global="South"
                if Global=="South":
                    lat,lon=utm.to_latlon(self.data.loc[index,"verbatimLatitude"], self.data.loc[index,"verbatimLongitude"], int(coordinate[zone_index].upper().replace("S","")), northern=False)
                elif Global=="North":
                    lat,lon=utm.to_latlon(self.data.loc[index,"verbatimLatitude"], self.data.loc[index,"verbatimLongitude"], int(coordinate[zone_index].upper().replace("N","")), northern=True)
                self.data.loc[index,"decimalLatitude"]="{0:.7f}".format(lat)
                self.data.loc[index,"decimalLongitude"]="{0:.7f}".format(lon)
                self.data.loc[index,"geodeticDatum"]="WGS84"
                #self.data.loc[index,"georeferenceSources"]="GeoParser Marcelo Oyaneder"
    
    def dms_to_dg(self):
        for index in self.data.index:
            if (self.data.loc[index,"verbatimCoordinateSystem"]=="degrees minutes seconds" or self.data.loc[index,"verbatimCoordinateSystem"]=="degrees decimal minutes") and self.data.loc[index,"verbatimCoordinates"] is not np.nan:
                try: 
                    location= self.data.loc[index,"verbatimCoordinates"]
                    if "O" in location.upper():
                        location=location.replace("O","W")
                    response=requests.get(f"http://data.canadensys.net/tools/coordinates.json?data=35|{location}&idprovided=TRUE").json()
                    lon,lat=response["features"][0]["geometry"]["coordinates"]
                    self.data.loc[index,"decimalLatitude"]="{0:.7f}".format(lat)
                    self.data.loc[index,"decimalLongitude"]="{0:.7f}".format(lon)
                    self.data.loc[index,"geodeticDatum"]="WGS84"
                    #self.data.loc[index,"georeferenceSources"]="GeoParser Marcelo Oyaneder | Canadensys"
                except:
                    self.data.loc[index,"decimalLatitude"]="Error"
                    self.data.loc[index,"decimalLongitude"]="Error"

                            

# TESTING...

In [5]:
data=pd.read_excel("coordenadas_SQF.xlsx")

data

occurrenceID  verbatimCoordinates verbatimLatitude  \
0       PBUCH:SQF:2955                  NaN              NaN   
1       PBUCH:SQF:3782                  NaN              NaN   
2       PBUCH:SQF:3783                  NaN              NaN   
3       PBUCH:SQF:3784                  NaN              NaN   
4       PBUCH:SQF:3785                  NaN              NaN   
5       PBUCH:SQF:3786                  NaN              NaN   
6       PBUCH:SQF:3789                  NaN              NaN   
7       PBUCH:SQF:3790                  NaN              NaN   
8       PBUCH:SQF:3791                  NaN              NaN   
9     PBUCH:SQF:3791H1                  NaN              NaN   
10      PBUCH:SQF:3792                  NaN              NaN   
11      PBUCH:SQF:3793                  NaN              NaN   
12      PBUCH:SQF:3796                  NaN              NaN   
13      PBUCH:SQF:3798                  NaN              NaN   
14      PBUCH:SQF:3799                  NaN              NaN   
15      PBUCH:SQF:3800                  NaN              NaN   
16      PBUCH:SQF:3802                  NaN              NaN   
17      PBUCH:SQF:3804                  NaN              NaN   
18      PBUCH:SQF:3805                  NaN              NaN   
19    PBUCH:SQF:3805H1                  NaN              NaN   
20      PBUCH:SQF:3807                  NaN              NaN   
21    PBUCH:SQF:3807H1                  NaN              NaN   
22      PBUCH:SQF:3808                  NaN              NaN   
23      PBUCH:SQF:3809                  NaN              NaN   
24      PBUCH:SQF:3810                  NaN              NaN   
25      PBUCH:SQF:3811                  NaN              NaN   
26      PBUCH:SQF:3812                  NaN              NaN   
27      PBUCH:SQF:3813                  NaN              NaN   
28    PBUCH:SQF:3813H1                  NaN              NaN   
29      PBUCH:SQF:3814                  NaN              NaN   
30      PBUCH:SQF:3815                  NaN              NaN   
31      PBUCH:SQF:3816                  NaN              NaN   
32      PBUCH:SQF:3817                  NaN              NaN   
33    PBUCH:SQF:3817H1                  NaN              NaN   
34      PBUCH:SQF:3818                  NaN              NaN   
35    PBUCH:SQF:3818H1                  NaN              NaN   
36      PBUCH:SQF:3821                  NaN              NaN   
37      PBUCH:SQF:3822                  NaN              NaN   
38    PBUCH:SQF:3822H1                  NaN              NaN   
39      PBUCH:SQF:3823                  NaN              NaN   
40      PBUCH:SQF:3824                  NaN              NaN   
41      PBUCH:SQF:3825                  NaN              NaN   
42      PBUCH:SQF:3826                  NaN              NaN   
43      PBUCH:SQF:3827                  NaN              NaN   
44      PBUCH:SQF:3828                  NaN              NaN   
45      PBUCH:SQF:3829                  NaN              NaN   
46      PBUCH:SQF:3830                  NaN              NaN   
47      PBUCH:SQF:3831                  NaN              NaN   
48      PBUCH:SQF:3832                  NaN              NaN   
49      PBUCH:SQF:3833                  NaN              NaN   
50      PBUCH:SQF:3837                  NaN              NaN   
51    PBUCH:SQF:3837H1                  NaN              NaN   
52      PBUCH:SQF:3838                  NaN              NaN   
53      PBUCH:SQF:3839                  NaN              NaN   
54      PBUCH:SQF:3840                  NaN              NaN   
55      PBUCH:SQF:3842                  NaN              NaN   
56      PBUCH:SQF:3843                  NaN              NaN   
57      PBUCH:SQF:3844                  NaN              NaN   
58      PBUCH:SQF:3845                  NaN              NaN   
59      PBUCH:SQF:3846                  NaN              NaN   
60    PBUCH:SQF:3846H1                  NaN              NaN   
61      PBUCH:SQF:3847                  Na

In [6]:
%%time
#Testing...

db_prep(data).verbatimCoordinates_autocomplete()
db_prep(data).verb_lat_long_autocomplete()
db_prep(data).verbatimCoordinateSystem_autocomplete()
db_prep(data).coordinatePrecision_autocomplete()
coord_transform(data).utm_to_dg()
coord_transform(data).dms_to_dg()


Wall time: 1min 3s


In [7]:
data

occurrenceID  verbatimCoordinates verbatimLatitude  \
0       PBUCH:SQF:2955                  NaN              NaN   
1       PBUCH:SQF:3782                  NaN              NaN   
2       PBUCH:SQF:3783                  NaN              NaN   
3       PBUCH:SQF:3784                  NaN              NaN   
4       PBUCH:SQF:3785                  NaN              NaN   
5       PBUCH:SQF:3786                  NaN              NaN   
6       PBUCH:SQF:3789                  NaN              NaN   
7       PBUCH:SQF:3790                  NaN              NaN   
8       PBUCH:SQF:3791                  NaN              NaN   
9     PBUCH:SQF:3791H1                  NaN              NaN   
10      PBUCH:SQF:3792                  NaN              NaN   
11      PBUCH:SQF:3793                  NaN              NaN   
12      PBUCH:SQF:3796                  NaN              NaN   
13      PBUCH:SQF:3798                  NaN              NaN   
14      PBUCH:SQF:3799                  NaN              NaN   
15      PBUCH:SQF:3800                  NaN              NaN   
16      PBUCH:SQF:3802                  NaN              NaN   
17      PBUCH:SQF:3804                  NaN              NaN   
18      PBUCH:SQF:3805                  NaN              NaN   
19    PBUCH:SQF:3805H1                  NaN              NaN   
20      PBUCH:SQF:3807                  NaN              NaN   
21    PBUCH:SQF:3807H1                  NaN              NaN   
22      PBUCH:SQF:3808                  NaN              NaN   
23      PBUCH:SQF:3809                  NaN              NaN   
24      PBUCH:SQF:3810                  NaN              NaN   
25      PBUCH:SQF:3811                  NaN              NaN   
26      PBUCH:SQF:3812                  NaN              NaN   
27      PBUCH:SQF:3813                  NaN              NaN   
28    PBUCH:SQF:3813H1                  NaN              NaN   
29      PBUCH:SQF:3814                  NaN              NaN   
30      PBUCH:SQF:3815                  NaN              NaN   
31      PBUCH:SQF:3816                  NaN              NaN   
32      PBUCH:SQF:3817                  NaN              NaN   
33    PBUCH:SQF:3817H1                  NaN              NaN   
34      PBUCH:SQF:3818                  NaN              NaN   
35    PBUCH:SQF:3818H1                  NaN              NaN   
36      PBUCH:SQF:3821                  NaN              NaN   
37      PBUCH:SQF:3822                  NaN              NaN   
38    PBUCH:SQF:3822H1                  NaN              NaN   
39      PBUCH:SQF:3823                  NaN              NaN   
40      PBUCH:SQF:3824                  NaN              NaN   
41      PBUCH:SQF:3825                  NaN              NaN   
42      PBUCH:SQF:3826                  NaN              NaN   
43      PBUCH:SQF:3827                  NaN              NaN   
44      PBUCH:SQF:3828                  NaN              NaN   
45      PBUCH:SQF:3829                  NaN              NaN   
46      PBUCH:SQF:3830                  NaN              NaN   
47      PBUCH:SQF:3831                  NaN              NaN   
48      PBUCH:SQF:3832                  NaN              NaN   
49      PBUCH:SQF:3833                  NaN              NaN   
50      PBUCH:SQF:3837                  NaN              NaN   
51    PBUCH:SQF:3837H1                  NaN              NaN   
52      PBUCH:SQF:3838                  NaN              NaN   
53      PBUCH:SQF:3839                  NaN              NaN   
54      PBUCH:SQF:3840                  NaN              NaN   
55      PBUCH:SQF:3842                  NaN              NaN   
56      PBUCH:SQF:3843                  NaN              NaN   
57      PBUCH:SQF:3844                  NaN              NaN   
58      PBUCH:SQF:3845                  NaN              NaN   
59      PBUCH:SQF:3846                  NaN              NaN   
60    PBUCH:SQF:3846H1                  NaN              NaN   
61      PBUCH:SQF:3847                  Na

In [8]:
%%time
# Testing ...

db_prep(data).location_autocomplete()
db_prep(data).continent_autocomplete()
db_prep(data).higherGeography_autocomplete()

0 exito
0 exito
0 exito
0 exito
0 exito
1 exito
1 exito
1 exito
1 exito
1 exito
1 exito
2 exito
2 exito
2 exito
2 exito
2 exito
3 exito
3 exito
3 exito
3 exito
3 exito
3 exito
4 exito
4 exito
4 exito
4 exito
4 exito
4 exito
5 exito
5 exito
5 exito
5 exito
5 exito
5 exito
6 exito
6 exito
6 exito
6 exito
6 exito
6 exito
6 exito
7 exito
7 exito
7 exito
7 exito
7 exito
7 exito
8 exito
8 exito
8 exito
8 exito
8 exito
9 exito
9 fail
10 exito
10 exito
10 exito
10 exito
10 exito
11 exito
11 exito
11 exito
11 exito
11 exito
12 exito
12 exito
12 exito
12 exito
12 exito
12 exito
13 exito
13 exito
13 exito
13 exito
13 exito
14 exito
14 exito
14 exito
14 exito
14 exito
15 exito
15 exito
15 exito
15 exito
15 exito
15 exito
16 exito
16 exito
16 exito
16 exito
16 exito
17 exito
17 exito
17 exito
17 exito
17 exito
18 exito
18 exito
18 exito
18 exito
18 exito
19 exito
19 fail
20 exito
20 exito
20 exito
20 exito
20 exito
21 exito
21 fail
22 exito
22 exito
22 exito
22 exito
22 exito
23 exito
23 exito
23 e

160 exito
160 exito
160 exito
160 exito
160 exito
160 exito
160 exito
161 exito
161 exito
161 exito
161 exito
161 exito
161 exito
161 exito
162 exito
162 exito
162 exito
162 exito
162 exito
162 exito
162 exito
163 exito
163 exito
163 exito
163 exito
163 exito
163 exito
163 exito
164 exito
164 exito
164 exito
164 exito
164 exito
165 exito
165 exito
165 exito
165 exito
165 exito
165 exito
165 exito
166 exito
166 exito
166 exito
166 exito
166 exito
167 exito
167 exito
167 exito
167 exito
167 exito
168 exito
168 exito
168 exito
168 exito
168 exito
168 exito
169 exito
169 exito
169 exito
169 exito
169 exito
170 exito
170 exito
170 exito
170 exito
170 exito
170 exito
170 exito
170 exito
170 exito
170 exito
171 exito
171 fail
172 exito
172 exito
172 exito
172 exito
172 exito
173 exito
173 exito
173 exito
173 exito
173 exito
174 exito
174 exito
174 exito
174 exito
174 exito
175 exito
175 exito
175 exito
175 exito
175 exito
176 exito
176 fail
177 exito
177 fail
178 exito
178 fail
179 exito
179 

298 exito
298 exito
298 exito
298 exito
298 exito
298 exito
299 exito
299 exito
299 exito
299 exito
299 exito
299 exito
300 exito
300 exito
300 exito
300 exito
300 exito
300 exito
301 exito
301 exito
301 exito
301 exito
301 exito
301 exito
301 exito
302 exito
302 exito
302 exito
302 exito
302 exito
302 exito
303 exito
303 exito
303 exito
303 exito
303 exito
303 exito
304 exito
304 exito
304 exito
304 exito
304 exito
304 exito
305 exito
305 exito
305 exito
305 exito
305 exito
305 exito
306 exito
306 exito
306 exito
306 exito
306 exito
306 exito
307 exito
307 exito
307 exito
307 exito
307 exito
307 exito
308 exito
308 exito
308 exito
308 exito
308 exito
308 exito
309 exito
309 exito
309 exito
309 exito
309 exito
309 exito
310 exito
310 exito
310 exito
310 exito
310 exito
310 exito
311 exito
311 exito
311 exito
311 exito
311 exito
311 exito
311 exito
311 exito
312 exito
312 exito
312 exito
312 exito
312 exito
312 exito
313 exito
313 fail
314 exito
314 exito
314 exito
314 exito
314 exito
3

416 exito
416 exito
416 exito
416 exito
416 exito
416 exito
416 exito
417 exito
417 exito
417 exito
417 exito
417 exito
417 exito
417 exito
418 exito
418 exito
418 exito
418 exito
418 exito
419 exito
419 exito
419 exito
419 exito
419 exito
420 exito
420 exito
420 exito
420 exito
420 exito
421 exito
421 exito
421 exito
421 exito
421 exito
422 exito
422 exito
422 exito
422 exito
422 exito
423 exito
423 exito
423 exito
423 exito
423 exito
424 exito
424 exito
424 exito
424 exito
424 exito
424 exito
425 exito
425 exito
425 exito
425 exito
425 exito
426 exito
426 exito
426 exito
426 exito
426 exito
427 exito
427 exito
427 exito
427 exito
427 exito
428 exito
428 exito
428 exito
428 exito
428 exito
428 exito
429 exito
429 exito
429 exito
429 exito
429 exito
429 exito
430 exito
430 exito
430 exito
430 exito
430 exito
431 exito
431 exito
431 exito
431 exito
431 exito
432 exito
432 exito
432 exito
432 exito
432 exito
433 exito
433 exito
433 exito
433 exito
433 exito
433 exito
434 exito
434 exito


566 exito
566 exito
566 exito
566 exito
566 exito
567 exito
567 exito
567 exito
567 exito
567 exito
568 exito
568 exito
568 exito
568 exito
568 exito
569 exito
569 exito
569 exito
569 exito
569 exito
570 exito
570 exito
570 exito
570 exito
570 exito
571 exito
571 exito
571 exito
571 exito
571 exito
572 exito
572 exito
572 exito
572 exito
572 exito
573 exito
573 exito
573 exito
573 exito
573 exito
574 exito
574 exito
574 exito
574 exito
574 exito
575 exito
575 exito
575 exito
575 exito
575 exito
576 exito
576 exito
576 exito
576 exito
576 exito
577 exito
577 exito
577 exito
577 exito
577 exito
578 exito
578 exito
578 exito
578 exito
578 exito
579 exito
579 exito
579 exito
579 exito
579 exito
580 exito
580 exito
580 exito
580 exito
580 exito
581 exito
581 exito
581 exito
581 exito
581 exito
582 exito
582 exito
582 exito
582 exito
582 exito
583 exito
583 exito
583 exito
583 exito
583 exito
584 exito
584 exito
584 exito
584 exito
584 exito
585 exito
585 exito
585 exito
585 exito
585 exito


...

2407 exito
2407 fail
2408 exito
2408 fail
2409 exito
2409 fail
2410 exito
2410 fail
2411 exito
2411 fail
2412 exito
2412 fail
2413 exito
2413 fail
2414 exito
2414 fail
2415 exito
2415 fail
2416 exito
2416 fail
2417 exito
2417 fail
2418 exito
2418 fail
2419 exito
2419 fail
2420 exito
2420 fail
2421 exito
2421 fail
2422 exito
2422 fail
2423 exito
2423 fail
2424 exito
2424 exito
2424 exito
2424 exito
2424 exito
2424 exito
2425 exito
2425 fail
2426 exito
2426 fail
2427 exito
2427 fail
2428 exito
2428 fail
2429 exito
2429 fail
2430 exito
2430 fail
2431 exito
2431 fail
2432 exito
2432 fail
2433 exito
2433 fail
2434 exito
2434 fail
2435 exito
2435 fail
2436 exito
2436 fail
2437 exito
2437 fail
2438 exito
2438 exito
2438 exito
2438 exito
2438 exito
2439 exito
2439 exito
2439 exito
2439 exito
2439 exito
2440 exito
2440 exito
2440 exito
2440 exito
2440 exito
2441 exito
2441 exito
2441 exito
2441 exito
2441 exito
2442 exito
2442 fail
2443 exito
2443 fail
2444 exito
2444 exito
2444 exito
2444 exit

2728 exito
2728 fail
2729 exito
2729 fail
2730 exito
2730 fail
2731 exito
2731 fail
2732 exito
2732 fail
2733 exito
2733 fail
2734 exito
2734 fail
2735 exito
2735 fail
2736 exito
2736 fail
2737 exito
2737 fail
2738 exito
2738 fail
2739 exito
2739 fail
2740 exito
2740 fail
2741 exito
2741 fail
2742 exito
2742 exito
2742 exito
2742 exito
2742 exito
2743 exito
2743 fail
2744 exito
2744 fail
2745 exito
2745 exito
2745 exito
2745 exito
2745 exito
2746 exito
2746 fail
2747 exito
2747 exito
2747 exito
2747 exito
2747 exito
2748 exito
2748 fail
2749 exito
2749 exito
2749 exito
2749 exito
2749 exito
2750 exito
2750 fail
2751 exito
2751 fail
2752 exito
2752 fail
2753 exito
2753 fail
2754 exito
2754 fail
2755 exito
2755 fail
2756 exito
2756 fail
2757 exito
2757 fail
2758 exito
2758 fail
2759 exito
2759 fail
2760 exito
2760 fail
2761 exito
2761 fail
2762 exito
2762 fail
2763 exito
2763 fail
2764 exito
2764 exito
2764 exito
2764 exito
2764 exito
2765 exito
2765 exito
2765 exito
2765 exito
2765 exit

3060 exito
3060 fail
3061 exito
3061 fail
3062 exito
3062 fail
3063 exito
3063 fail
3064 exito
3064 fail
3065 exito
3065 fail
3066 exito
3066 fail
3067 exito
3067 fail
3068 exito
3068 fail
3069 exito
3069 fail
3070 exito
3070 fail
3071 exito
3071 fail
3072 exito
3072 fail
3073 exito
3073 exito
3073 exito
3073 exito
3073 exito
3074 exito
3074 exito
3074 exito
3074 exito
3074 exito
3074 exito
3074 exito
3075 exito
3075 fail
3076 exito
3076 fail
3077 exito
3077 fail
3078 exito
3078 exito
3078 exito
3078 exito
3078 exito
3078 exito
3079 exito
3079 fail
3080 exito
3080 fail
3081 exito
3081 fail
3082 exito
3082 exito
3082 exito
3082 exito
3082 exito
3082 exito
3082 exito
3082 exito
3083 exito
3083 fail
3084 exito
3084 fail
3085 exito
3085 fail
3086 exito
3086 fail
3087 exito
3087 exito
3087 exito
3087 exito
3087 exito
3087 exito
3087 exito
3088 exito
3088 fail
3089 exito
3089 fail
3090 exito
3090 fail
3091 exito
3091 exito
3091 exito
3091 exito
3091 exito
3092 exito
3092 fail
3093 exito
3093

3412 exito
3412 fail
3413 exito
3413 fail
3414 exito
3414 exito
3414 exito
3414 exito
3414 exito
3415 exito
3415 fail
3416 exito
3416 fail
3417 exito
3417 fail
3418 exito
3418 fail
3419 exito
3419 fail
3420 exito
3420 fail
3421 exito
3421 fail
3422 exito
3422 fail
3423 exito
3423 fail
3424 exito
3424 fail
3425 exito
3425 exito
3425 exito
3425 exito
3425 exito
3426 exito
3426 fail
3427 exito
3427 fail
3428 exito
3428 fail
3429 exito
3429 fail
3430 exito
3430 fail
3431 exito
3431 fail
3432 exito
3432 fail
3433 exito
3433 exito
3433 exito
3433 exito
3433 exito
3434 exito
3434 exito
3434 exito
3434 exito
3434 exito
3435 exito
3435 fail
3436 exito
3436 exito
3436 exito
3436 exito
3436 exito
3437 exito
3437 exito
3437 exito
3437 exito
3437 exito
3438 exito
3438 exito
3438 exito
3438 exito
3438 exito
3439 exito
3439 fail
3440 exito
3440 fail
3441 exito
3441 fail
3442 exito
3442 exito
3442 exito
3442 exito
3442 exito
3443 exito
3443 fail
3444 exito
3444 exito
3444 exito
3444 exito
3444 exito
3

3727 exito
3727 fail
3728 exito
3728 fail
3729 exito
3729 fail
3730 exito
3730 fail
3731 exito
3731 fail
3732 exito
3732 fail
3733 exito
3733 fail
3734 exito
3734 fail
3735 exito
3735 fail
3736 exito
3736 fail
3737 exito
3737 fail
3738 exito
3738 fail
3739 exito
3739 fail
3740 exito
3740 fail
3741 exito
3741 fail
3742 exito
3742 fail
3743 exito
3743 fail
3744 exito
3744 fail
3745 exito
3745 fail
3746 exito
3746 fail
3747 exito
3747 fail
3748 exito
3748 fail
3749 exito
3749 fail
3750 exito
3750 fail
3751 exito
3751 fail
3752 exito
3752 fail
3753 exito
3753 fail
3754 exito
3754 fail
3755 exito
3755 fail
3756 exito
3756 fail
3757 exito
3757 fail
3758 exito
3758 fail
3759 exito
3759 fail
3760 exito
3760 fail
3761 exito
3761 fail
3762 exito
3762 fail
3763 exito
3763 fail
3764 exito
3764 fail
3765 exito
3765 fail
3766 exito
3766 fail
3767 exito
3767 fail
3768 exito
3768 fail
3769 exito
3769 fail
3770 exito
3770 fail
3771 exito
3771 fail
3772 exito
3772 fail
3773 exito
3773 fail
3774 exito
37

In [13]:
data

occurrenceID  verbatimCoordinates verbatimLatitude  \
0       PBUCH:SQF:2955                  NaN              NaN   
1       PBUCH:SQF:3782                  NaN              NaN   
2       PBUCH:SQF:3783                  NaN              NaN   
3       PBUCH:SQF:3784                  NaN              NaN   
4       PBUCH:SQF:3785                  NaN              NaN   
5       PBUCH:SQF:3786                  NaN              NaN   
6       PBUCH:SQF:3789                  NaN              NaN   
7       PBUCH:SQF:3790                  NaN              NaN   
8       PBUCH:SQF:3791                  NaN              NaN   
9     PBUCH:SQF:3791H1                  NaN              NaN   
10      PBUCH:SQF:3792                  NaN              NaN   
11      PBUCH:SQF:3793                  NaN              NaN   
12      PBUCH:SQF:3796                  NaN              NaN   
13      PBUCH:SQF:3798                  NaN              NaN   
14      PBUCH:SQF:3799                  NaN              NaN   
15      PBUCH:SQF:3800                  NaN              NaN   
16      PBUCH:SQF:3802                  NaN              NaN   
17      PBUCH:SQF:3804                  NaN              NaN   
18      PBUCH:SQF:3805                  NaN              NaN   
19    PBUCH:SQF:3805H1                  NaN              NaN   
20      PBUCH:SQF:3807                  NaN              NaN   
21    PBUCH:SQF:3807H1                  NaN              NaN   
22      PBUCH:SQF:3808                  NaN              NaN   
23      PBUCH:SQF:3809                  NaN              NaN   
24      PBUCH:SQF:3810                  NaN              NaN   
25      PBUCH:SQF:3811                  NaN              NaN   
26      PBUCH:SQF:3812                  NaN              NaN   
27      PBUCH:SQF:3813                  NaN              NaN   
28    PBUCH:SQF:3813H1                  NaN              NaN   
29      PBUCH:SQF:3814                  NaN              NaN   
30      PBUCH:SQF:3815                  NaN              NaN   
31      PBUCH:SQF:3816                  NaN              NaN   
32      PBUCH:SQF:3817                  NaN              NaN   
33    PBUCH:SQF:3817H1                  NaN              NaN   
34      PBUCH:SQF:3818                  NaN              NaN   
35    PBUCH:SQF:3818H1                  NaN              NaN   
36      PBUCH:SQF:3821                  NaN              NaN   
37      PBUCH:SQF:3822                  NaN              NaN   
38    PBUCH:SQF:3822H1                  NaN              NaN   
39      PBUCH:SQF:3823                  NaN              NaN   
40      PBUCH:SQF:3824                  NaN              NaN   
41      PBUCH:SQF:3825                  NaN              NaN   
42      PBUCH:SQF:3826                  NaN              NaN   
43      PBUCH:SQF:3827                  NaN              NaN   
44      PBUCH:SQF:3828                  NaN              NaN   
45      PBUCH:SQF:3829                  NaN              NaN   
46      PBUCH:SQF:3830                  NaN              NaN   
47      PBUCH:SQF:3831                  NaN              NaN   
48      PBUCH:SQF:3832                  NaN              NaN   
49      PBUCH:SQF:3833                  NaN              NaN   
50      PBUCH:SQF:3837                  NaN              NaN   
51    PBUCH:SQF:3837H1                  NaN              NaN   
52      PBUCH:SQF:3838                  NaN              NaN   
53      PBUCH:SQF:3839                  NaN              NaN   
54      PBUCH:SQF:3840                  NaN              NaN   
55      PBUCH:SQF:3842                  NaN              NaN   
56      PBUCH:SQF:3843                  NaN              NaN   
57      PBUCH:SQF:3844                  NaN              NaN   
58      PBUCH:SQF:3845                  NaN              NaN   
59      PBUCH:SQF:3846                  NaN              NaN   
60    PBUCH:SQF:3846H1                  NaN              NaN   
61      PBUCH:SQF:3847                  Na

In [10]:
#data.to_excel("coordenadas_SQF_result.xlsx",index=False)


# Find Country Test

In [11]:
import requests

result=requests.get(f"https://api.gbif-uat.org/v1/geocode/reverse?lat=-33.2167&lng=-70.7833").json()


In [12]:
result=requests.get(f"https://api.gbif-uat.org/v1/geocode/reverse?lat={lat}&lng={lon}").json()
for elements in result:
    if elements["source"]=="http://gadm.org/":
        if elements["type"]=="GADM0":
            self.data.loc[index,"country"]=elements["title"]
            self.data.loc[index,"countryCode"]=elements["isoCountryCode2Digit"]
        elif elements["type"]=="GADM1": self.data.loc[index,"stateProvince"]=elements["title"]
        elif elements["type"]=="GADM2": self.data.loc[index,"county"]=elements["title"]
        elif elements["type"]=="GADM3": self.data.loc[index,"municipality"]=elements["title"]


NameError: name 'lat' is not defined

In [ ]:
import requests

lat,lon=-33.2167, -70.7833
result=requests.get(f"https://nominatim.openstreetmap.org/reverse?format=json&lat={lat}&lon={lon}&polygon_text=1").json()
result

    def location_autocomplete(self): #include country, country_code, stateProvince, county, municipality 
        geolocator = Nominatim(user_agent="GeoParser")
        for index in self.data.index:
            try:
                lat=self.data.loc[index,"decimalLatitude"]
                lon=self.data.loc[index,"decimalLongitude"]
                location=geolocator.reverse(f"{lat},{lon}")
                self.data.loc[index,"country"]=location.raw["address"]["country"]
                #if self.data.loc[index,"georeferenceSources"] == "GeoParser Marcelo Oyaneder | Canadensys":
                #    self.data.loc[index,"georeferenceSources"]="GeoParser Marcelo Oyaneder | GeoPy | Canadensys"
                #else: self.data.loc[index,"georeferenceSources"]="GeoParser Marcelo Oyaneder | GeoPy"
                #if set(['locality']).issubset(set(self.data.columns.to_list())) is True and np.isnan(self.data.loc[index,"locality"]):
                #    self.data.loc[index,"locality"]= location.raw["display_name"]
                #elif set(['locality']).issubset(set(self.data.columns.to_list())) is False:
                #    self.data["locality"]=np.nan
                #    self.data.loc[index,"locality"]= location.raw["display_name"]
                self.data.loc[index,"countryCode"]=location.raw["address"]["country_code"].upper()
                self.data.loc[index,"stateProvince"]=location.raw["address"]["state"]
                self.data.loc[index,"county"]=location.raw["address"]["county"]
                if list(location.raw["address"].values())[-5] != location.raw["address"]["county"]:
                    self.data.loc[index,"municipality"]=list(location.raw["address"].values())[-5]
            except: pass

In [ ]:
from shapely.wkt import loads as load_wkt


In [ ]:
location= "32° 46'S, 71° 32'O"